In [38]:
import numpy as np # library to handle data in a vectorized manner
import pandas as pd # library for data analsysis
import json # library to handle JSON files
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe
import matplotlib
import matplotlib.pyplot as plt
import matplotlib.cm as cm
import matplotlib.colors as colors
from sklearn.cluster import KMeans
from sklearn.preprocessing import StandardScaler
import folium # map rendering library

In [2]:
#df1=pd.read_csv(r'NYPD_Arrests_Data__Historic_.csv')

In [3]:
#df1.head()

In [4]:
#df1.columns.values

In [5]:
#df1.drop(['PD_CD','KY_CD','LAW_CAT_CD','AGE_GROUP','PERP_SEX','PERP_RACE','X_COORD_CD','Y_COORD_CD'],axis=1,inplace=True)

In [6]:
#df1.head()

In [7]:
#df1.to_csv('arrest_record_by_precinct.csv',index=0)

The few lines of codes above were for one time use to cut down the size of the dataset. Please uncomment if you wish to restart from the original dataset.

In [8]:
df_arrest_data=pd.read_csv(r'arrest_record_by_precinct.csv')

In [9]:
df_arrest_data.head()

ARREST_KEY ARREST_DATE                               PD_DESC  \
0   173130602  12/31/2017                 MARIJUANA, POSSESSION   
1   173114463  12/31/2017       THEFT OF SERVICES, UNCLASSIFIED   
2   173113513  12/31/2017  NY STATE LAWS,UNCLASSIFIED VIOLATION   
3   173113423  12/31/2017                             ASSAULT 3   
4   173113421  12/31/2017                             ASSAULT 3   

                         OFNS_DESC    LAW_CODE ARREST_BORO  ARREST_PRECINCT  \
0          MISCELLANEOUS PENAL LAW  PL 2210500           Q              105   
1  OTHER OFFENSES RELATED TO THEFT  PL 1651503           Q              114   
2                 OTHER STATE LAWS  LOC000000V           K               73   
3     ASSAULT 3 & RELATED OFFENSES  PL 1200001           M               18   
4     ASSAULT 3 & RELATED OFFENSES  PL 1200001           M               18   

   JURISDICTION_CODE   Latitude  Longitude  
0                0.0  40.735772 -73.715638  
1                0.0  40.769437 -73.910241  
2                1.0  40.679525 -73.904572  
3                0.0  40.763523 -73.987074  
4                0.0  40.759768 -73.989811

The next two lines explores the different ways to combined multiple logic statements to select values from a column in pandas.

In [10]:
dfx=df_arrest_data[df_arrest_data['ARREST_PRECINCT']==105]
dfx[dfx['PD_DESC']=='MARIJUANA, POSSESSION'].ARREST_KEY.count()

336

In [11]:
df_arrest_data[(df_arrest_data['ARREST_PRECINCT']==105)&(df_arrest_data['PD_DESC']=='MARIJUANA, POSSESSION')].ARREST_KEY.count()

336

Let's take a look at the unique values of some of the fields before going any further.

In [12]:
df_ofns_list=pd.DataFrame(df_arrest_data.OFNS_DESC.unique())

In [13]:
df_ofns_list

0
0           MISCELLANEOUS PENAL LAW
1   OTHER OFFENSES RELATED TO THEFT
2                  OTHER STATE LAWS
3      ASSAULT 3 & RELATED OFFENSES
4                           ROBBERY
..                              ...
82   DISRUPTION OF A RELIGIOUS SERV
83   LOITERING/GAMBLING (CARDS, DIC
84                       KIDNAPPING
85  NYS LAWS-UNCLASSIFIED VIOLATION
86   UNLAWFUL POSS. WEAP. ON SCHOOL

[87 rows x 1 columns]

We create a copy of df_ofns_list to carry on further analysis.

In [14]:
df_offense=df_ofns_list.copy()

In [15]:
df_offense=df_offense.T
df_offense.columns=df_offense.iloc[0]

In [16]:
df_offense

0  MISCELLANEOUS PENAL LAW  OTHER OFFENSES RELATED TO THEFT  OTHER STATE LAWS  \
0  MISCELLANEOUS PENAL LAW  OTHER OFFENSES RELATED TO THEFT  OTHER STATE LAWS   

0  ASSAULT 3 & RELATED OFFENSES  ROBBERY  DANGEROUS DRUGS  \
0  ASSAULT 3 & RELATED OFFENSES  ROBBERY  DANGEROUS DRUGS   

0  OFFENSES INVOLVING FRAUD  PETIT LARCENY  FELONY ASSAULT  DANGEROUS WEAPONS  \
0  OFFENSES INVOLVING FRAUD  PETIT LARCENY  FELONY ASSAULT  DANGEROUS WEAPONS   

0  ...  OTHER OFFENSES RELATED TO THEF  HOMICIDE-NEGLIGENT,UNCLASSIFIE  \
0  ...  OTHER OFFENSES RELATED TO THEF  HOMICIDE-NEGLIGENT,UNCLASSIFIE   

0  THEFT OF SERVICES  FOR OTHER AUTHORITIES  \
0  THEFT OF SERVICES  FOR OTHER AUTHORITIES   

0  AGRICULTURE & MRKTS LAW-UNCLASSIFIED  DISRUPTION OF A RELIGIOUS SERV  \
0  AGRICULTURE & MRKTS LAW-UNCLASSIFIED  DISRUPTION OF A RELIGIOUS SERV   

0  LOITERING/GAMBLING (CARDS, DIC  KIDNAPPING  \
0  LOITERING/GAMBLING (CARDS, DIC  KIDNAPPING   

0  NYS LAWS-UNCLASSIFIED VIOLATION  UNLAWFUL POSS. WEAP. ON SCHOOL  
0  NYS LAWS-UNCLASSIFIED VIOLATION  UNLAWFUL POSS. WEAP. ON SCHOOL  

[1 rows x 87 columns]

In [17]:
df_offense.drop(df_offense.index[0],inplace=True)

In [18]:
df_offense.head()

Empty DataFrame
Columns: [MISCELLANEOUS PENAL LAW, OTHER OFFENSES RELATED TO THEFT, OTHER STATE LAWS, ASSAULT 3 & RELATED OFFENSES, ROBBERY, DANGEROUS DRUGS, OFFENSES INVOLVING FRAUD, PETIT LARCENY, FELONY ASSAULT, DANGEROUS WEAPONS, OFF. AGNST PUB ORD SENSBLTY & RGHTS TO PRIV, INTOXICATED/IMPAIRED DRIVING, INTOXICATED & IMPAIRED DRIVING, CRIMINAL MISCHIEF & RELATED OFFENSES, GRAND LARCENY, VEHICLE AND TRAFFIC LAWS, BURGLARY, OFFENSES AGAINST PUBLIC ADMINISTRATION, OTHER TRAFFIC INFRACTION, SEX CRIMES, ARSON, CRIMINAL TRESPASS, BURGLAR'S TOOLS, ALCOHOLIC BEVERAGE CONTROL LAW, UNAUTHORIZED USE OF A VEHICLE 3 (UUV), FORGERY, OTHER STATE LAWS (NON PENAL LAW), ENDAN WELFARE INCOMP, OFF. AGNST PUB ORD SENSBLTY &, FRAUDS, PROSTITUTION & RELATED OFFENSES, OFFENSES AGAINST THE PERSON, POSSESSION OF STOLEN PROPERTY 5, OFFENSES AGAINST PUBLIC SAFETY, OFFENSES RELATED TO CHILDREN, ADMINISTRATIVE CODE, GRAND LARCENY OF MOTOR VEHICLE, DISORDERLY CONDUCT, RAPE, nan, POSSESSION OF STOLEN PROPERTY, FORCIBLE TOUCHING, F.C.A. P.I.N.O.S., MURDER & NON-NEGL. MANSLAUGHTER, MOVING INFRACTIONS, HOMICIDE-NEGLIGENT,UNCLASSIFIED, CRIMINAL MISCHIEF & RELATED OF, GAMBLING, HARRASSMENT 2, CHILD ABANDONMENT/NON SUPPORT 1, JOSTLING, ANTICIPATORY OFFENSES, FRAUDULENT ACCOSTING, OTHER STATE LAWS (NON PENAL LA, THEFT-FRAUD, ADMINISTRATIVE CODES, KIDNAPPING & RELATED OFFENSES, PARKING OFFENSES, LOITERING, LOITERING FOR DRUG PURPOSES, LOITERING/GAMBLING (CARDS, DICE, ETC), UNLAWFUL POSS. WEAP. ON SCHOOL GROUNDS, ABORTION, NEW YORK CITY HEALTH CODE, CHILD ABANDONMENT/NON SUPPORT, ESCAPE 3, HOMICIDE-NEGLIGENT-VEHICLE, DISRUPTION OF A RELIGIOUS SERVICE, UNDER THE INFLUENCE, DRUGS, HARASSMENT, FORTUNE TELLING, LOITERING,BEGGING, OFFENSES AGAINST MARRIAGE UNCLASSIFIED, NYS LAWS-UNCLASSIFIED FELONY, MURDER & NON-NEGL. MANSLAUGHTE, OFFENSES AGAINST PUBLIC ADMINI, UNAUTHORIZED USE OF A VEHICLE, OTHER OFFENSES RELATED TO THEF, HOMICIDE-NEGLIGENT,UNCLASSIFIE, THEFT OF SERVICES, FOR OTHER AUTHORITIES, AGRICULTURE & MRKTS LAW-UNCLASSIFIED, DISRUPTION OF A RELIGIOUS SERV, LOITERING/GAMBLING (CARDS, DIC, KIDNAPPING, NYS LAWS-UNCLASSIFIED VIOLATION, UNLAWFUL POSS. WEAP. ON SCHOOL]
Index: []

[0 rows x 87 columns]

In [19]:
df_offense.insert(loc=0,column='PRECINCT',value='')
df_offense

Empty DataFrame
Columns: [PRECINCT, MISCELLANEOUS PENAL LAW, OTHER OFFENSES RELATED TO THEFT, OTHER STATE LAWS, ASSAULT 3 & RELATED OFFENSES, ROBBERY, DANGEROUS DRUGS, OFFENSES INVOLVING FRAUD, PETIT LARCENY, FELONY ASSAULT, DANGEROUS WEAPONS, OFF. AGNST PUB ORD SENSBLTY & RGHTS TO PRIV, INTOXICATED/IMPAIRED DRIVING, INTOXICATED & IMPAIRED DRIVING, CRIMINAL MISCHIEF & RELATED OFFENSES, GRAND LARCENY, VEHICLE AND TRAFFIC LAWS, BURGLARY, OFFENSES AGAINST PUBLIC ADMINISTRATION, OTHER TRAFFIC INFRACTION, SEX CRIMES, ARSON, CRIMINAL TRESPASS, BURGLAR'S TOOLS, ALCOHOLIC BEVERAGE CONTROL LAW, UNAUTHORIZED USE OF A VEHICLE 3 (UUV), FORGERY, OTHER STATE LAWS (NON PENAL LAW), ENDAN WELFARE INCOMP, OFF. AGNST PUB ORD SENSBLTY &, FRAUDS, PROSTITUTION & RELATED OFFENSES, OFFENSES AGAINST THE PERSON, POSSESSION OF STOLEN PROPERTY 5, OFFENSES AGAINST PUBLIC SAFETY, OFFENSES RELATED TO CHILDREN, ADMINISTRATIVE CODE, GRAND LARCENY OF MOTOR VEHICLE, DISORDERLY CONDUCT, RAPE, nan, POSSESSION OF STOLEN PROPERTY, FORCIBLE TOUCHING, F.C.A. P.I.N.O.S., MURDER & NON-NEGL. MANSLAUGHTER, MOVING INFRACTIONS, HOMICIDE-NEGLIGENT,UNCLASSIFIED, CRIMINAL MISCHIEF & RELATED OF, GAMBLING, HARRASSMENT 2, CHILD ABANDONMENT/NON SUPPORT 1, JOSTLING, ANTICIPATORY OFFENSES, FRAUDULENT ACCOSTING, OTHER STATE LAWS (NON PENAL LA, THEFT-FRAUD, ADMINISTRATIVE CODES, KIDNAPPING & RELATED OFFENSES, PARKING OFFENSES, LOITERING, LOITERING FOR DRUG PURPOSES, LOITERING/GAMBLING (CARDS, DICE, ETC), UNLAWFUL POSS. WEAP. ON SCHOOL GROUNDS, ABORTION, NEW YORK CITY HEALTH CODE, CHILD ABANDONMENT/NON SUPPORT, ESCAPE 3, HOMICIDE-NEGLIGENT-VEHICLE, DISRUPTION OF A RELIGIOUS SERVICE, UNDER THE INFLUENCE, DRUGS, HARASSMENT, FORTUNE TELLING, LOITERING,BEGGING, OFFENSES AGAINST MARRIAGE UNCLASSIFIED, NYS LAWS-UNCLASSIFIED FELONY, MURDER & NON-NEGL. MANSLAUGHTE, OFFENSES AGAINST PUBLIC ADMINI, UNAUTHORIZED USE OF A VEHICLE, OTHER OFFENSES RELATED TO THEF, HOMICIDE-NEGLIGENT,UNCLASSIFIE, THEFT OF SERVICES, FOR OTHER AUTHORITIES, AGRICULTURE & MRKTS LAW-UNCLASSIFIED, DISRUPTION OF A RELIGIOUS SERV, LOITERING/GAMBLING (CARDS, DIC, KIDNAPPING, NYS LAWS-UNCLASSIFIED VIOLATION, UNLAWFUL POSS. WEAP. ON SCHOOL]
Index: []

[0 rows x 88 columns]

In [20]:
df_offense[['PRECINCT']]=pd.DataFrame(df_arrest_data['ARREST_PRECINCT'].unique())

In [21]:
df_offense

0   PRECINCT MISCELLANEOUS PENAL LAW OTHER OFFENSES RELATED TO THEFT  \
0        105                     NaN                             NaN   
1        114                     NaN                             NaN   
2         73                     NaN                             NaN   
3         18                     NaN                             NaN   
4          9                     NaN                             NaN   
..       ...                     ...                             ...   
73        10                     NaN                             NaN   
74        50                     NaN                             NaN   
75        26                     NaN                             NaN   
76        22                     NaN                             NaN   
77        27                     NaN                             NaN   

0  OTHER STATE LAWS ASSAULT 3 & RELATED OFFENSES ROBBERY DANGEROUS DRUGS  \
0               NaN                          NaN     NaN             NaN   
1               NaN                          NaN     NaN             NaN   
2               NaN                          NaN     NaN             NaN   
3               NaN                          NaN     NaN             NaN   
4               NaN                          NaN     NaN             NaN   
..              ...                          ...     ...             ...   
73              NaN                          NaN     NaN             NaN   
74              NaN                          NaN     NaN             NaN   
75              NaN                          NaN     NaN             NaN   
76              NaN                          NaN     NaN             NaN   
77              NaN                          NaN     NaN             NaN   

0  OFFENSES INVOLVING FRAUD PETIT LARCENY FELONY ASSAULT  ...  \
0                       NaN           NaN            NaN  ...   
1                       NaN           NaN            NaN  ...   
2                       NaN           NaN            NaN  ...   
3                       NaN           NaN            NaN  ...   
4                       NaN           NaN            NaN  ...   
..                      ...           ...            ...  ...   
73                      NaN           NaN            NaN  ...   
74                      NaN           NaN            NaN  ...   
75                      NaN           NaN            NaN  ...   
76                      NaN           NaN            NaN  ...   
77                      NaN           NaN            NaN  ...   

0  OTHER OFFENSES RELATED TO THEF HOMICIDE-NEGLIGENT,UNCLASSIFIE  \
0                             NaN                            NaN   
1                             NaN                            NaN   
2                             NaN                            NaN   
3                             NaN                            NaN   
4                             NaN                            NaN   
..                            ...                            ...   
73                            NaN                            NaN   
74                            NaN                            NaN   
75                            NaN                            NaN   
76                            NaN                            NaN   
77                            NaN                            NaN   

0  THEFT OF SERVICES FOR OTHER AUTHORITIES  \
0                NaN                   NaN   
1                NaN                   NaN   
2                NaN                   NaN   
3                NaN                   NaN   
4                NaN                   NaN   
..               ...                   ...   
73               NaN                   NaN   
74               NaN                   NaN   
75               NaN                   NaN   
76               NaN                   NaN   
77               NaN                   NaN   

0  AGRICULTURE & MRKTS LAW-UNCLASSIFIED DISRUPTION OF A RELIGIOUS SERV 

In [22]:
i=0
while i<len(df_offense.index):
    precinct=df_offense.iloc[i,0]
    dx=df_arrest_data[df_arrest_data['ARREST_PRECINCT']==precinct]
    #print(precinct)
    j=1
    while j<len(df_offense.columns):
        df_offense.iloc[i,j]=(dx[dx['OFNS_DESC']==df_offense.columns.values[j]]).shape[0]
        j+=1
    i+=1

In [23]:
df_offense

0   PRECINCT  MISCELLANEOUS PENAL LAW  OTHER OFFENSES RELATED TO THEFT  \
0        105                     4187                               69   
1        114                     3882                             2044   
2         73                     5836                             8496   
3         18                      964                             4401   
4          9                     1412                             3458   
..       ...                      ...                              ...   
73        10                     1035                             2411   
74        50                      675                              493   
75        26                     1131                             5603   
76        22                       96                                5   
77        27                        0                                0   

0   OTHER STATE LAWS  ASSAULT 3 & RELATED OFFENSES  ROBBERY  DANGEROUS DRUGS  \
0               1001                          8326     2126            11649   
1               3706                          9340     2319            14876   
2              14536                         11669     3258            36830   
3               6684                          4579     1242             8088   
4               2777                          4427     1203            11508   
..               ...                           ...      ...              ...   
73              2119                          2969     1064             7450   
74               389                          4337      938             6043   
75              3416                          2703     1229             5839   
76               133                           267      234             1303   
77                 0                             0        0                1   

0   OFFENSES INVOLVING FRAUD  PETIT LARCENY  FELONY ASSAULT  ...  \
0                        118            967            3210  ...   
1                        220           2847            3236  ...   
2                        343           2773            5666  ...   
3                       1259           5568            1536  ...   
4                        191           2494            1717  ...   
..                       ...            ...             ...  ...   
73                       195           1233            1248  ...   
74                       160           1469            1347  ...   
75                        78           1266            1090  ...   
76                        23            162              81  ...   
77                         0              0               0  ...   

0   OTHER OFFENSES RELATED TO THEF  HOMICIDE-NEGLIGENT,UNCLASSIFIE  \
0                                7                               0   
1                               17                               0   
2                              122                               1   
3                              120                               0   
4                               51                               0   
..                             ...                             ...   
73                              18                               0   
74                               8                               0   
75                              37                               0   
76                               0                               0   
77                               0                               0   

0   THEFT OF SERVICES  FOR OTHER AUTHORITIES  \
0                   0                     11   
1                   0                     20   
2                   9                      5   
3                   7                     19   
4                   2                      6   
..                ...                    ...   
73                  0                    122   
74                  0                     22   
75                  5                      6   
76          

Calculating df_offense was very memory intensive. Let's save it as a csv before going any further. Doing it just once is all we need.

In [24]:
#df_offense.to_csv('Crimes_by_category_and_precinct.csv',index=0)

In [25]:
df_offense=pd.read_csv('Crimes_by_category_and_precinct.csv')
df_offense.head()

PRECINCT  MISCELLANEOUS PENAL LAW  OTHER OFFENSES RELATED TO THEFT  \
0       105                     4187                               69   
1       114                     3882                             2044   
2        73                     5836                             8496   
3        18                      964                             4401   
4         9                     1412                             3458   

   OTHER STATE LAWS  ASSAULT 3 & RELATED OFFENSES  ROBBERY  DANGEROUS DRUGS  \
0              1001                          8326     2126            11649   
1              3706                          9340     2319            14876   
2             14536                         11669     3258            36830   
3              6684                          4579     1242             8088   
4              2777                          4427     1203            11508   

   OFFENSES INVOLVING FRAUD  PETIT LARCENY  FELONY ASSAULT  ...  \
0                       118            967            3210  ...   
1                       220           2847            3236  ...   
2                       343           2773            5666  ...   
3                      1259           5568            1536  ...   
4                       191           2494            1717  ...   

   OTHER OFFENSES RELATED TO THEF  HOMICIDE-NEGLIGENT,UNCLASSIFIE  \
0                               7                               0   
1                              17                               0   
2                             122                               1   
3                             120                               0   
4                              51                               0   

   THEFT OF SERVICES  FOR OTHER AUTHORITIES  \
0                  0                     11   
1                  0                     20   
2                  9                      5   
3                  7                     19   
4                  2                      6   

   AGRICULTURE & MRKTS LAW-UNCLASSIFIED  DISRUPTION OF A RELIGIOUS SERV  \
0                                     6                               0   
1                                     3                               0   
2                                     4                               0   
3                                     1                               0   
4                                     1                               1   

   LOITERING/GAMBLING (CARDS, DIC  KIDNAPPING  \
0                               0           0   
1                               0           0   
2                               0           1   
3                               0           0   
4                               0           0   

   NYS LAWS-UNCLASSIFIED VIOLATION  UNLAWFUL POSS. WEAP. ON SCHOOL  
0                                0                               0  
1                                0                               0  
2                                0                               0  
3                                0                               1  
4                                0                               0  

[5 rows x 88 columns]

In [26]:
df_offense.columns.tolist()

['PRECINCT',
 'MISCELLANEOUS PENAL LAW',
 'OTHER OFFENSES RELATED TO THEFT',
 'OTHER STATE LAWS',
 'ASSAULT 3 & RELATED OFFENSES',
 'ROBBERY',
 'DANGEROUS DRUGS',
 'OFFENSES INVOLVING FRAUD',
 'PETIT LARCENY',
 'FELONY ASSAULT',
 'DANGEROUS WEAPONS',
 'OFF. AGNST PUB ORD SENSBLTY & RGHTS TO PRIV',
 'INTOXICATED/IMPAIRED DRIVING',
 'INTOXICATED & IMPAIRED DRIVING',
 'CRIMINAL MISCHIEF & RELATED OFFENSES',
 'GRAND LARCENY',
 'VEHICLE AND TRAFFIC LAWS',
 'BURGLARY',
 'OFFENSES AGAINST PUBLIC ADMINISTRATION',
 'OTHER TRAFFIC INFRACTION',
 'SEX CRIMES',
 'ARSON',
 'CRIMINAL TRESPASS',
 "BURGLAR'S TOOLS",
 'ALCOHOLIC BEVERAGE CONTROL LAW',
 'UNAUTHORIZED USE OF A VEHICLE 3 (UUV)',
 'FORGERY',
 'OTHER STATE LAWS (NON PENAL LAW)',
 'ENDAN WELFARE INCOMP',
 'OFF. AGNST PUB ORD SENSBLTY &',
 'FRAUDS',
 'PROSTITUTION & RELATED OFFENSES',
 'OFFENSES AGAINST THE PERSON',
 'POSSESSION OF STOLEN PROPERTY 5',
 'OFFENSES AGAINST PUBLIC SAFETY',
 'OFFENSES RELATED TO CHILDREN',
 'ADMINISTRATIVE CODE',
 

In [32]:
df_offense=df_offense[['PRECINCT','ASSAULT 3 & RELATED OFFENSES','ROBBERY','FELONY ASSAULT','BURGLARY','CRIMINAL TRESPASS','GRAND LARCENY OF MOTOR VEHICLE','MURDER & NON-NEGL. MANSLAUGHTER','MURDER & NON-NEGL. MANSLAUGHTE']].copy()

For unknown reason, precinct 27 is part of the dataset. Since Precinct 27 does not exist in reality, let's remove row 27.

In [33]:
#df_offense=df_offense.drop(df_offense.index[-1]).copy()

In [34]:
df_offense

PRECINCT  ASSAULT 3 & RELATED OFFENSES  ROBBERY  FELONY ASSAULT  BURGLARY  \
0        105                          8326     2126            3210      1198   
1        114                          9340     2319            3236       993   
2         73                         11669     3258            5666      1205   
3         18                          4579     1242            1536      1295   
4          9                          4427     1203            1717       843   
..       ...                           ...      ...             ...       ...   
72        13                          4090     1386            1704      1259   
73        10                          2969     1064            1248       549   
74        50                          4337      938            1347       474   
75        26                          2703     1229            1090       472   
76        22                           267      234              81         8   

    CRIMINAL TRESPASS  GRAND LARCENY OF MOTOR VEHICLE  \
0                 562                             676   
1                3321                             264   
2                5055                             445   
3                1139                              32   
4                3624                              81   
..                ...                             ...   
72               1310                              54   
73               2127                              46   
74               1305                              75   
75               2148                              92   
76                 16                               2   

    MURDER & NON-NEGL. MANSLAUGHTER  MURDER & NON-NEGL. MANSLAUGHTE  
0                               260                              10  
1                               258                              13  
2                               360                              18  
3                                45                               5  
4                                66                               5  
..                              ...                             ...  
72                               58                               2  
73                               45                               7  
74                              129                              33  
75                               92                               5  
76                                1                               1  

[77 rows x 9 columns]

The reason for having 8 columns is to make sure the differences between the precinct are large enough to differentiate relative safety. Let's add across rows and save them under a new column.

In [36]:
df_offense['Total']=df_offense.sum(axis=1)
df_offense.sort_values(by='Total', ascending=False, inplace=True)
df_offense

PRECINCT  ASSAULT 3 & RELATED OFFENSES  ROBBERY  FELONY ASSAULT  BURGLARY  \
32        40                         14709     4074            5277       931   
56        75                         18529     5808            8481      1955   
25        44                         14940     4551            6264      1329   
28        43                         16402     4172            5028      1032   
36        46                         13861     3455            4966       919   
..       ...                           ...      ...             ...       ...   
13       121                          2394      388            1060       371   
62       111                          2113      709             684       500   
7         17                          2173      426             642       498   
61       123                          2189      247             543       312   
76        22                           267      234              81         8   

    CRIMINAL TRESPASS  GRAND LARCENY OF MOTOR VEHICLE  \
32              15494                             224   
56               4097                             807   
25              10884                             319   
28              10243                             313   
36               8631                             212   
..                ...                             ...   
13                193                              85   
62                307                             101   
7                 585                              33   
61                199                              61   
76                 16                               2   

    MURDER & NON-NEGL. MANSLAUGHTER  MURDER & NON-NEGL. MANSLAUGHTE  Total  
32                              456                              75  82560  
56                              297                              30  80158  
25                              564                              55  77900  
28                              253                              14  75000  
36                              374                              37  65002  
..                              ...                             ...    ...  
13                               49                               6   9334  
62                               23                               5   9106  
7                                12                               1   8774  
61                                8                               1   7366  
76                                1                               1   1264  

[77 rows x 10 columns]

In [40]:
city='New York, New York, United States of America'
geolocator=Nominatim(user_agent="nyc_explorer")
location=geolocator.geocode(city)
lat=location.latitude
lon=location.longitude
lat,lon

(40.7127281, -74.0060152)

In [41]:
NYC_crime_map=folium.Map(location=[lat,lon],zoom_start=11)

NYC_geo=r'police_precincts.geojson' #GeoJson File

NYC_crime_map.choropleth(geo_data=NYC_geo,data=df_offense,columns=['PRECINCT','Total'],key_on='feature.properties.Precinct',fill_color='YlOrRd',fill_opacity=0.7,line_opacity=0.2,legend_name="Selected Crimes")

NYC_crime_map

/home/user-1131/venv/lib/python3.6/site-packages/folium/folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning
